*Import librairies*

In [1]:
import pandas as pd
import numpy as np
import json
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.io as pio
import plotly.offline as pyo
from scipy.optimize import minimize
import statsmodels.api as sm

pio.templates.default = "plotly_dark"
pd.set_option("display.max_columns", 101)

*Import Custom Functions*

In [49]:
from zozipop import StocksData, zoziPlot, zPlotly_theme

# ESSAY 1

## Summary Table
 - [Introduction](#introduction)
    - [Stocks](#stocks)
    - [Statistics about stocks returns](#stats)
      - [Statistics about normal stocks returns](#stats_normal)
      - [Statistics about log stocks returns](#stats_logs)
    - [Graphs about stocks](#graphs)
      - [Prices](#price)
      - [Candles Chart](#candles)
      - [Prices Vs. Returns](#price_return)
 - [Question 1](#question_1)
    - [Correlation Matrix](#correlation)
    - [CoVariance Matrix](#covariance)
    - [10 Correlation Coefficients Stats](#10corrstats)
    - [10 Correlation Coefficients Graph](#10corrgraph)
 - [Question 2](#question_2)
 - [Question 3](#question_3)
    - [Max Sharpe Ratio Portfolio Vs. Min Volatility](#maxsharpevsminvol)
    - [Max Sharpe Ratio Portfolio Stats & Allocation](#maxsharpestats)
    - [Efficient Frontier](#efficient_frontier)
 - [Question 4](#question_4)
    - [CAPM Graph](#capmgraph)
 - [Question 5](#question_5)
    - [Fama-French 3 Factors Model Graph](#ff3graph)
 - [Question 6](#question_6)
    - [Indexed Prices Graph](#indexedgraph)

<a id="summary"><a/>

## Introduction <a id='introduction'></a>

### Stocks <a id='stocks'></a>

In [3]:
with open('data/stocks.json', 'r') as fp:
    stocks = json.load(fp)
stocks

{'Materials': {'Name': 'Newmont Corporation', 'Ticker': 'NEM'},
 'Communication Services': {'Name': 'Alphabet Inc.', 'Ticker': 'GOOGL'},
 'Consumer Discretionary': {'Name': 'Amazon.com Inc.', 'Ticker': 'AMZN'},
 'Consumer Staples': {'Name': 'PepsiCo Inc.', 'Ticker': 'PEP'},
 'Energy': {'Name': 'National Oilwell Varco Inc.', 'Ticker': 'NOV'},
 'Financial Services': {'Name': 'Bank of America Corp', 'Ticker': 'BAC'},
 'Healthcare': {'Name': 'HCA Healthcare', 'Ticker': 'HCA'},
 'Industrials': {'Name': 'Boeing Company', 'Ticker': 'BA'},
 'Real Estate': {'Name': 'Host Hotels & Resorts', 'Ticker': 'HST'},
 'Information Technology': {'Name': 'Apple Inc.', 'Ticker': 'AAPL'},
 'Utilities': {'Name': 'American Electric Power', 'Ticker': 'AEP'}}

### Read data

In [4]:
complete_data = pd.read_csv(
    'data/complete_data.csv', header=[0, 1], index_col=[0])

In [5]:
market = pd.read_csv('data/market.csv', index_col=[0])

In [6]:
stocks_object = StocksData(complete_data, market)
zp = zoziPlot(900, 600)

In [7]:
stocks_object.get('complete_data')['AAPL']

Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-06-29   46.572498   46.797501   45.727501   46.277500   44.964947   
2018-07-02   45.955002   46.825001   45.855000   46.794998   45.467773   
2018-07-03   46.947498   46.987499   45.884998   45.980000   44.675892   
2018-07-05   46.314999   46.602501   46.070000   46.349998   45.035393   
2018-07-06   46.355000   47.107498   46.299999   46.992500   45.659668   
...                ...         ...         ...         ...         ...   
2020-10-21  116.669998  118.709999  116.449997  116.870003  116.870003   
2020-10-22  117.449997  118.040001  114.589996  115.750000  115.750000   
2020-10-23  116.389999  116.550003  114.279999  115.040001  115.040001   
2020-10-26  114.010002  116.550003  112.879997  115.050003  115.050003   
2020-10-27  115.489998  117.279999  114.540001  116.599998  116.599998   

                 Volume  
Date                     
2018-06-29   90950800.0  
2018-07-02   70925200.0  
2018-07-03   55819200.0  
2018-07-05   66416800.0  
2018-07-06   69940800.0  
...                 ...  
2020-10-21   89946000.0  
2020-10-22  101988000.0  
2020-10-23   82572600.0  
2020-10-26  111850700.0  
2020-10-27   91927700.0  

[587 rows x 6 columns]

### Statistics about stocks <a id='stats'></a>

In [8]:
stocks_object.get('complete_data').describe(include='all')

HCA                                                  \
             Open        High         Low       Close   Adj Close   
count  587.000000  587.000000  587.000000  587.000000  587.000000   
mean   126.864497  128.588943  125.068722  126.820954  125.716139   
std     14.597232   14.083259   15.036820   14.619520   14.336877   
min     67.000000   74.209999   58.380001   68.129997   68.129997   
25%    120.935001  122.560001  119.215000  120.915001  120.243168   
50%    130.039993  131.759995  128.410004  130.009995  128.369995   
75%    136.355003  138.229996  134.600006  136.215004  135.312836   
max    151.639999  151.970001  149.500000  151.039993  150.530045   

                            PEP                                      \
             Volume        Open        High         Low       Close   
count  5.870000e+02  587.000000  587.000000  587.000000  587.000000   
mean   1.939768e+06  127.115128  128.199864  125.975792  127.134361   
std    1.038509e+06   10.887277   10.857319   10.870716   10.877834   
min    4.550000e+05  105.199997  105.760002  101.419998  103.930000   
25%    1.215600e+06  115.855000  116.739998  114.889999  115.885002   
50%    1.643200e+06  131.419998  132.440002  130.009995  131.220001   
75%    2.345150e+06  136.159996  136.974998  134.935005  135.959999   
max    7.008100e+06  147.110001  147.199997  145.940002  146.990005   

                                        AEP                          \
        Adj Close        Volume        Open        High         Low   
count  587.000000  5.870000e+02  587.000000  587.000000  587.000000   
mean   123.193310  4.871038e+06   83.873799   84.685707   83.026303   
std     12.492000  2.360348e+06    8.371279    8.402083    8.421042   
min     99.063225  1.220600e+06   68.639999   69.239998   65.139999   
25%    110.147434  3.519750e+06   77.494999   78.599998   76.700001   
50%    128.149872  4.301500e+06   83.750000   84.699997   82.849998   
75%    133.186195  5.524950e+06   90.529999   91.240002   89.740002   
max    143.845245  2.755970e+07  104.470001  104.970001  103.860001   

                                                    HST              \
            Close   Adj Close        Volume        Open        High   
count  587.000000  587.000000  5.870000e+02  587.000000  587.000000   
mean    83.928194   81.216788  2.731579e+06   16.420818   16.617342   
std      8.375294    9.073230  1.370110e+06    3.518129    3.470348   
min     68.870003   63.994541  4.401000e+05    9.130000    9.700000   
25%     77.750000   74.612312  2.020750e+06   12.340000   12.655000   
50%     83.660004   81.550003  2.411700e+06   17.450001   17.570000   
75%     90.530003   88.004597  3.107700e+06   19.000000   19.195001   
max    104.330002  102.555588  2.245570e+07   21.940001   22.059999   

                                                               GOOGL  \
              Low       Close   Adj Close        Volume         Open   
count  587.000000  587.000000  587.000000  5.870000e+02   587.000000   
mean    16.187462   16.400273   15.707650  8.476309e+06  1262.312828   
std      3.579859    3.518214    3.032482  4.558733e+06   156.238214   
min      7.860000    9.060000    9.060000  1.251900e+06   984.320007   
25%     11.910000   12.265000   12.244539  5.527700e+06  1137.674988   
50%     17.260000   17.430000   16.674925  7.459300e+06  1220.660034   
75%     18.795000   18.995000   17.918624  9.961750e+06  1389.325012   
max     21.570000   21.940001   20.303028  3.428470e+07  1699.520020   

                                                                         \
              High          Low        Close    Adj Close        Volume   
count   587.000000   587.000000   587.000000   587.000000  5.870000e+02   
mean   1275.915757  1248.903613  1263.082129  1263.082129  1.817421e+06   
std     157.654878   155.418888   156.721781   156.721781  8.492448e+05   
min    1012.119995   977.659973   984.669983   984.669983  6.401000e+05   
25%    1150.365051 

#### Normal returns <a id='stats_normal'></a>

In [9]:
stocks_stats = stocks_object.get_statistics()

In [10]:
stocks_stats

Std  Annual Std    Mean  Geometric Mean  Median      Min      Max  \
AAPL    2.3389     37.1285  0.1901         50.6464  0.2024 -12.8647  11.9808   
AEP     1.7322     27.4976  0.0770         16.9063  0.1406 -11.5827  11.6826   
AMZN    2.1537     34.1882  0.1357         32.7775  0.1459  -7.9221   9.4452   
BA      3.7846     60.0786 -0.0531        -27.0190 -0.0576 -23.8484  24.3186   
BAC     2.5912     41.1335  0.0141         -4.7858  0.0810 -15.3974  17.7962   
GOOGL   1.9924     31.6280  0.0792         16.1331  0.1211 -11.6342   9.6202   
HCA     2.8059     44.5416  0.0839         11.9163  0.1100 -19.0161  22.5598   
HST     2.6713     42.4050 -0.0643        -22.2495 -0.0265 -15.6880  17.0974   
NEM     2.2422     35.5932  0.1198         26.9840  0.1570 -11.1161  14.0182   
NOV     3.8301     60.8006 -0.1987        -49.8271 -0.1369 -28.9541  21.4876   
PEP     1.6954     26.9135  0.0677         14.3683  0.0664 -11.4283  12.9366   
Market  1.5755     25.0096  0.0502          9.9699  0.1075 -11.9841   9.3828   

         Kurtosis  Skewness     Alpha      Beta  VaR 95% HS  VaR 95% DN  \
AAPL     5.608353 -0.163762 -0.000532  0.543678     -3.2594     -3.6570   
AEP     13.386894 -0.010800  0.000118  0.499053     -2.2376     -2.7722   
AMZN     2.422439  0.105631 -0.000139  0.472659     -3.2948     -3.4068   
BA      12.146194  0.271573  0.000648  0.274997     -4.8461     -6.2782   
BAC     10.810570  0.238862  0.000432  0.497214     -3.9743     -4.2480   
GOOGL    5.579783 -0.139928 -0.000004  0.639096     -3.0039     -3.1979   
HCA     13.591212  0.437826  0.000204  0.355172     -3.6475     -4.5314   
HST      8.422540  0.394651  0.000745  0.378548     -3.8926     -4.4581   
NEM      8.141356  0.404131  0.000325  0.147589     -3.3226     -3.5682   
NOV      9.387814 -0.308378  0.001015  0.258193     -5.6634     -6.4986   
PEP     18.963003 -0.044369  0.000034  0.691958     -2.1180     -2.7210   
Market  14.277263 -0.601046  0.000000  1.000000     -2.4028     -2.5412   

        Systemic Risk  
AAPL           0.0073  
AEP            0.0062  
AMZN           0.0055  
BA             0.0019  
BAC            0.0061  
GOOGL          0.0101  
HCA            0.0031  
HST            0.0036  
NEM            0.0005  
NOV            0.0017  
PEP            0.0119  
Market         0.0248

#### Log Returns <a id='stats_logs'></a>

In [11]:
stocks_stats_logs = stocks_object.get_statistics(logs=True)

In [12]:
stocks_stats_logs

Std  Annual Std    Mean  Geometric Mean  Median      Min      Max  \
AAPL    2.3438     37.2061  0.1626         40.4846  0.2021 -13.7708  11.3157   
AEP     1.7348     27.5388  0.0620         12.5332  0.1405 -12.3103  11.0491   
AMZN    2.1506     34.1401  0.1125         25.2569  0.1458  -8.2535   9.0254   
BA      3.8044     60.3928 -0.1250        -39.4967 -0.0577 -27.2444  21.7677   
BAC     2.5933     41.1679 -0.0195        -12.5783  0.0810 -16.7205  16.3786   
GOOGL   1.9966     31.6946  0.0594         10.4185  0.1211 -12.3685   9.1852   
HCA     2.8022     44.4834  0.0447          1.2971  0.1099 -21.0920  20.3429   
HST     2.6684     42.3592 -0.0999        -28.9584 -0.0265 -17.0646  15.7836   
NEM     2.2347     35.4750  0.0948         19.2434  0.1569 -11.7839  13.1188   
NOV     3.8953     61.8358 -0.2737        -58.9596 -0.1370 -34.1844  19.4642   
PEP     1.6997     26.9822  0.0533         10.2476  0.0664 -12.1358  12.1656   
Market  1.5852     25.1640  0.0377          6.5062  0.1075 -12.7652   8.9683   

         Kurtosis  Skewness     Alpha      Beta  VaR 95% HS  VaR 95% DN  \
AAPL     5.861205 -0.430168 -0.000513  0.547134     -3.3137     -3.6925   
AEP     13.202776 -0.402762  0.000068  0.499455     -2.2631     -2.7915   
AMZN     2.402189 -0.035645 -0.000160  0.477461     -3.3504     -3.4250   
BA      12.954671 -0.541743  0.000729  0.281307     -4.9675     -6.3827   
BAC     10.566756 -0.246637  0.000475  0.501199     -4.0555     -4.2851   
GOOGL    5.800185 -0.366486 -0.000005  0.643298     -3.0500     -3.2247   
HCA     13.033766 -0.191520  0.000214  0.366209     -3.7157     -4.5645   
HST      8.131155 -0.009311  0.000764  0.387025     -3.9704     -4.4890   
NEM      7.474150  0.082294  0.000240  0.145003     -3.3791     -3.5810   
NOV     13.007749 -1.042878  0.001084  0.258252     -5.8301     -6.6809   
PEP     19.540604 -0.578095  0.000006  0.695880     -2.1407     -2.7425   
Market  15.368012 -0.983146  0.000000  1.000000     -2.4322     -2.5697   

        Systemic Risk  
AAPL           0.0075  
AEP            0.0063  
AMZN           0.0057  
BA             0.0020  
BAC            0.0063  
GOOGL          0.0104  
HCA            0.0034  
HST            0.0038  
NEM            0.0005  
NOV            0.0017  
PEP            0.0122  
Market         0.0251

### Graphs about Stocks <a id="graphs"></a>

#### Prices Analysis <a id='price'></a>

In [13]:
prices = stocks_object.get('prices')
zp.plot_comparative_prices(prices)

#### Candles Analysis <a id='candles'></a>

In [14]:
zp.plot_comparative_candles(complete_data)

#### Prices & Returns Analysis <a id='price_return'></a>

In [15]:
returns = stocks_object.get('returns')
zp.plot_comparative_prices_ret(prices, returns)

## Question 1 <a id='question_1'></a>

In [16]:
returns = stocks_object.get('returns')
cov = returns.cov()
corr = returns.corr()

### Correlation Matrix <a id='correlation'></a>

In [17]:
zp.plot_heatmap(corr, 'Correlation Matrix', round=2, gap=10)

### CoVariance Matrix <a id='covariance'></a>

In [18]:
zp.plot_heatmap(cov, 'Covariance Matrix', round=4, gap=5)

### 10 Correlations Coefficients Stats <a id='10corrstats'></a>

In [19]:
pairs_corr_std = stocks_object.question1([['HCA', 'HST'], ['AMZN', 'AAPL'], ['BAC', 'BA'], ['NOV', 'GOOGL']])
pairs_corr_std

HCA, HST            AMZN, AAPL              BAC, BA            \
       Returns        Std    Returns        Std   Returns       Std   
-1.0  0.041934  0.0672953   0.067838  0.0926092  0.007029  0.596714   
-0.8  0.041934   0.868358   0.067838   0.715744  0.007029   1.15617   
-0.6  0.041934     1.2262   0.067838    1.00797  0.007029   1.52229   
-0.4  0.041934    1.50103   0.067838    1.23277  0.007029   1.81605   
-0.2  0.041934     1.7328   0.067838    1.42247  0.007029    2.0685   
-0.0  0.041934    1.93704   0.067838     1.5897  0.007029   2.29332   
 0.2  0.041934    2.12171   0.067838    1.74093  0.007029   2.49799   
 0.4  0.041934    2.29154   0.067838    1.88004  0.007029   2.68712   
 0.6  0.041934    2.44963   0.067838    2.00955  0.007029   2.86379   
 0.8  0.041934    2.59811   0.067838    2.13119  0.007029   3.03017   
 1.0  0.041934    2.73856   0.067838    2.24626  0.007029   3.18788   

     NOV, GOOGL            
        Returns       Std  
-1.0  -0.099329  0.918849  
-0.8  -0.099329   1.26782  
-0.6  -0.099329   1.53963  
-0.4  -0.099329   1.77019  
-0.2  -0.099329     1.974  
-0.0  -0.099329   2.15865  
 0.2  -0.099329    2.3287  
 0.4  -0.099329   2.48716  
 0.6  -0.099329    2.6361  
 0.8  -0.099329   2.77707  
 1.0  -0.099329   2.91123

### 10 Correlations Coefficients Graph <a id='10corrgraph'></a>

In [20]:
zp.plot_corr_vs_std(pairs_corr_std)

## Question 2 <a id='question_2'></a>

### Equal Weighted Portfolio

In [21]:
eq_w_portfolio_stats = stocks_object.get_statistics_eq_w_portfolio()
eq_w_portfolio_stats

Std  Annual Std   Mean  Geometric Mean  Median      Min  \
Eq W Returns  1.7481     27.7505  0.041          6.6709  0.0894 -11.8637   

               Max  Kurtosis  Skewness     Alpha      Beta  VaR 95% HS  \
Eq W Returns  10.0  12.51529 -0.699272  0.000027  0.853119     -2.3074   

              VaR 95% DN  Systemic Risk  
Eq W Returns     -2.8344         0.0183

In [22]:
w = [1/len(stocks)]*len(stocks)
opt_eq_w = stocks_object.get_ret_vol_sr(stocks_object.get('returns'), w)

pd.DataFrame(data=[i.round(2) for i in opt_eq_w*[100, 100, 1]],
            index=['Returns', 'Volatility', 'Sharpe Ratio'],
            columns=['Stats About Eq W Portfolio']).T

Returns  Volatility  Sharpe Ratio
Stats About Eq W Portfolio    10.34       27.75          0.37

## Question 3 <a id='question_3'></a>

### Efficient portfolio

In [48]:
stocks

{'Materials': {'Name': 'Newmont Corporation', 'Ticker': 'NEM'},
 'Communication Services': {'Name': 'Alphabet Inc.', 'Ticker': 'GOOGL'},
 'Consumer Discretionary': {'Name': 'Amazon.com Inc.', 'Ticker': 'AMZN'},
 'Consumer Staples': {'Name': 'PepsiCo Inc.', 'Ticker': 'PEP'},
 'Energy': {'Name': 'National Oilwell Varco Inc.', 'Ticker': 'NOV'},
 'Financial Services': {'Name': 'Bank of America Corp', 'Ticker': 'BAC'},
 'Healthcare': {'Name': 'HCA Healthcare', 'Ticker': 'HCA'},
 'Industrials': {'Name': 'Boeing Company', 'Ticker': 'BA'},
 'Real Estate': {'Name': 'Host Hotels & Resorts', 'Ticker': 'HST'},
 'Information Technology': {'Name': 'Apple Inc.', 'Ticker': 'AAPL'},
 'Utilities': {'Name': 'American Electric Power', 'Ticker': 'AEP'}}

#### Selection of 3 to 5 stocks

In [24]:
stocks_names = [stocks[stock]['Ticker'] for stock in stocks]

In [25]:
%%time
findings = stocks_object.find_optimal_portfolio(3, 6, stocks_names)
findings

Wall time: 22.6 s


{'3 Stocks': {'Sharpe Ratio': 1.4540752736218556,
  'Stocks': ['NEM', 'AMZN', 'AAPL']},
 '4 Stocks': {'Sharpe Ratio': 1.4616359395907659,
  'Stocks': ['NEM', 'AMZN', 'AAPL', 'AEP']},
 '5 Stocks': {'Sharpe Ratio': 1.461636433704469,
  'Stocks': ['NEM', 'AMZN', 'HCA', 'AAPL', 'AEP']}}

In [26]:
selection = findings['4 Stocks']['Stocks']

In [27]:
sim, alloc = stocks_object.monte_carlo(selection, 2000, debug=True)

### Max Sharpe Ratio Portfolio Vs Min Volatility Portfolio <a id='maxsharpevsminvol'></a>

In [28]:
alloc

NEM   AMZN   AAPL    AEP  Returns  Volatility  \
Max Sharpe Allocation      29.51  13.17  47.76   9.56    38.15       26.11   
Min Volatility Allocation  23.65  31.14   1.11  44.09    26.88       21.56   

                           Sharpe Ratio  
Max Sharpe Allocation              1.46  
Min Volatility Allocation          1.25

### Stats about Max Sharpe Ratio Portfolio <a id='maxsharpestats'></a>

In [29]:
max_sr_ret = stocks_object.get_statistics_portfolio(selection, alloc.iloc[0, :4].values/100)
max_sr_ret

Std  Annual Std    Mean  Geometric Mean  Median     Min  \
Portfolio Returns  1.645     26.1141  0.1514         41.5219  0.1854 -7.5381   

                      Max  Kurtosis  Skewness     Alpha      Beta  VaR 95% HS  \
Portfolio Returns  9.4663  6.178886  0.123144 -0.000657  0.765392     -2.5562   

                   VaR 95% DN  Systemic Risk  
Portfolio Returns     -2.5545         0.0145

### Efficient Frontier <a id="efficient_frontier"><a/>

In [30]:
zp.plot_efficient_frontier(sim, alloc)

In [31]:
opt = stocks_object.maximize_sharpe_ratio(selection)

In [32]:
pd.DataFrame(data=[i.round(2) for i in opt[0]*[100, 100, 1]],
            index=['Returns', 'Volatility', 'Sharpe Ratio'],
            columns=['Stats']).T

Returns  Volatility  Sharpe Ratio
Stats    37.79       25.86          1.46

In [33]:
pd.DataFrame(data=[i.round(2) for i in opt[1]*100],
            index=selection,
            columns=['Allocation']).T

NEM   AMZN   AAPL    AEP
Allocation  30.99  12.04  46.54  10.44

## Question 4 <a id='question_4'></a>

### Regression with the market with CAPM

In [34]:
ff3_factor = pd.read_csv('data/F-F_Research_Data_Factors_daily.CSV')
max_sharpe_port_ret = stocks_object.compute_returns_portfolio(selection, opt[1]).rename('Returns')

In [35]:
data_capm = stocks_object.regression(portfolio_ret=max_sharpe_port_ret, ff3_factors=ff3_factor, include_ff3=False)


                  CAPM  
------------------------
Intercept      0.0012***
               (0.0004) 
MKT            0.7869***
               (0.0497) 
R-squared      0.6243   
R-squared Adj. 0.6236   
N              546      
Adjusted R2    0.6236   
Standard errors in
parentheses.
* p<.1, ** p<.05,
***p<.01


In [36]:
data_capm['DataFrame']['Results']

CAPMcoeff  CAPMtstat
Intercept   0.001168   2.740239
MKT         0.786851  15.846100

### Graph <a id='capmgraph'></a>

In [37]:
zp.plot_regression(data_capm['DataFrame']['Portfolio_Factors'], data_capm['Factors']['CAPM'], 'Capital Asset Pricing Model')

## Question 5 <a id='question_5'></a>

### CAPM as 3FF

In [38]:
data_ff3 = stocks_object.regression(portfolio_ret=max_sharpe_port_ret, ff3_factors=ff3_factor, include_ff3=True)


                  CAPM      FF3    
-----------------------------------
Intercept      0.0012*** 0.0008**  
               (0.0004)  (0.0004)  
MKT            0.7869*** 0.8499*** 
               (0.0497)  (0.0537)  
SMB                      -0.1096   
                         (0.0877)  
HML                      -0.3759***
                         (0.0449)  
R-squared      0.6243    0.6911    
R-squared Adj. 0.6236    0.6894    
N              546       546       
Adjusted R2    0.6236    0.6894    
Standard errors in parentheses.
* p<.1, ** p<.05, ***p<.01


In [39]:
data_ff3['DataFrame']['Results']

CAPMcoeff  CAPMtstat  FF3coeff   FF3tstat
Intercept   0.001168   2.740239  0.000763   1.988345
MKT         0.786851  15.846100  0.849949  15.831499
SMB              NaN        NaN -0.109600  -1.250188
HML              NaN        NaN -0.375880  -8.374361

### Graph <a id='ff3graph'></a>

In [40]:
zp.plot_regression(data_ff3['DataFrame']['Portfolio_Factors'], data_ff3['Factors']['Fama-French'], 'Fama-French 3 Factors Model')

## Question 6 <a id='question_6'></a>

### Analysis 30-days window :

In [43]:
market_returns = stocks_object.get('market_returns').rename('S&P500')
stocks_maxsharpe_port = stocks_object.get('returns')[selection]
max_sharpe_port_ret = max_sharpe_port_ret.rename('MaxSharpe Portfolio')

global_df = pd.concat([market_returns, max_sharpe_port_ret, stocks_maxsharpe_port], axis=1)

### Indexed Prices Graph <a id="indexedgraph"><a/>

In [47]:
zp.plot_time_window(global_df, '2020-02-13', '2020-03-15')